In [1]:
import pandas as pd
import numpy as np
import re
import scispacy
import spacy
from collections import Counter
import tqdm
from tqdm import tqdm
pd.set_option('display.max_colwidth', None)

In [2]:
icd10_def=pd.read_csv("Data MIMIC III/Data1.0/icd10_def.csv")

In [3]:
admid_icd=pd.read_csv("Data MIMIC III/DIAGNOSES_ICD.csv")

In [4]:
discharge=pd.read_csv("Data MIMIC III/discharge_summary_notes.csv")

In [5]:
discharge_icd=pd.read_csv("Data MIMIC III/Data1.0/notes_icd.csv")

In [6]:
def category(x):
    y=re.split("(\d{3}|[VE]\d{2})",x,1)
    return [y[1], y[2]]

In [7]:
def category10(x):
    y=re.search("[A-Z]\d{2}",x)
    if y:
        z=re.split("([A-Z]\d{2})",x,1)
        return [z[1], z[2]]
    else:
        return [None,None]    

In [8]:
def spliticdstring(x):
    return list(set(re.split(",",x)))

In [9]:
icd10_def

ICD9_CODE  ICD10  \
0        4019    I10   
1        4280   I509   
2       42731  I4891   
3       41401  I2510   
4        5849   N179   
..        ...    ...   
115     42833  I5033   
116     07054   B182   
117     42732  I4892   
118     E8782   Y832   
119     V1046  Z8546   

                                                                                                                                                                                        long_title  
0                                                                                                                                                                 ESSENTIAL (PRIMARY) HYPERTENSION  
1                                                                                                                                                                       HEART FAILURE, UNSPECIFIED  
2                                                                                                                                                                  UNSPECIFIED ATRIAL FIBRILLATION  
3                                                                                                                  ATHEROSCLEROTIC HEART DISEASE OF NATIVE CORONARY ARTERY WITHOUT ANGINA PECTORIS  
4                                                                                                                                                                ACUTE KIDNEY FAILURE, UNSPECIFIED  
..                                                                                                                                                                                             ...  
115                                                                                                                                          ACUTE ON CHRONIC DIASTOLIC (CONGESTIVE) HEART FAILURE  
116                                                                                                                                                                      CHRONIC VIRAL HEPATITIS C  
117                                                                                                                                                                     UNSPECIFIED ATRIAL FLUTTER  
118  SURGICAL OPERATION WITH ANASTOMOSIS, BYPASS OR GRAFT AS THE CAUSE OF ABNORMAL REACTION OF THE PATIENT, OR OF LATER COMPLICATION, WITHOUT MENTION OF MISADVENTURE AT THE TIME OF THE PROCEDURE  
119                                                                                                                                             PERSONAL HISTORY OF MALIGNANT NEOPLASM OF PROSTATE  

[120 rows x 3 columns]

In [10]:
icd10_def['icd9_div']=icd10_def.ICD9_CODE.apply(category)

In [11]:
icd10_def['icd10_div']=icd10_def.ICD10.apply(category10)

In [12]:
icd10_def[['icd9cat','icd9specific']]=icd10_def.icd9_div.apply(pd.Series)

In [13]:
icd10_def[['icd10cat','icd10specific']]=icd10_def.icd10_div.apply(pd.Series)

In [14]:
icd10_def

ICD9_CODE  ICD10  \
0        4019    I10   
1        4280   I509   
2       42731  I4891   
3       41401  I2510   
4        5849   N179   
..        ...    ...   
115     42833  I5033   
116     07054   B182   
117     42732  I4892   
118     E8782   Y832   
119     V1046  Z8546   

                                                                                                                                                                                        long_title  \
0                                                                                                                                                                 ESSENTIAL (PRIMARY) HYPERTENSION   
1                                                                                                                                                                       HEART FAILURE, UNSPECIFIED   
2                                                                                                                                                                  UNSPECIFIED ATRIAL FIBRILLATION   
3                                                                                                                  ATHEROSCLEROTIC HEART DISEASE OF NATIVE CORONARY ARTERY WITHOUT ANGINA PECTORIS   
4                                                                                                                                                                ACUTE KIDNEY FAILURE, UNSPECIFIED   
..                                                                                                                                                                                             ...   
115                                                                                                                                          ACUTE ON CHRONIC DIASTOLIC (CONGESTIVE) HEART FAILURE   
116                                                                                                                                                                      CHRONIC VIRAL HEPATITIS C   
117                                                                                                                                                                     UNSPECIFIED ATRIAL FLUTTER   
118  SURGICAL OPERATION WITH ANASTOMOSIS, BYPASS OR GRAFT AS THE CAUSE OF ABNORMAL REACTION OF THE PATIENT, OR OF LATER COMPLICATION, WITHOUT MENTION OF MISADVENTURE AT THE TIME OF THE PROCEDURE   
119                                                                                                                                             PERSONAL HISTORY OF MALIGNANT NEOPLASM OF PROSTATE   

      icd9_div  icd10_div icd9cat icd9specific icd10cat icd10specific  
0     [401, 9]    [I10, ]     401            9      I10                
1     [428, 0]   [I50, 9]     428            0      I50             9  
2    [427, 31]  [I48, 91]     427           31      I48            91  
3    [414, 01]  [I25, 10]     414           01      I25            10  
4     [584, 9]   [N17, 9]     584            9      N17             9  
..         ...        ...     ...          ...      ...           ...  
115  [428, 33]  [I50, 33]     428           33      I50            33  
116  [070, 54]   [B18, 2]     070           54      B18             2  
117  [427, 32]  [I48, 92]     427           32      I48            92  
118  [E87, 82]   [Y83, 2]     E87           82      Y83             2  
119  [V10, 46]  [Z85, 46]     V10           46      Z85            46  

[120 rows x 9 columns]

In [15]:
print(admid_icd[admid_icd.ICD9_CODE.isna()].ROW_ID.count())
print(admid_icd[admid_icd.HADM_ID.isna()].ROW_ID.count())

47
0


In [16]:
admid_icd.dropna(subset=['ICD9_CODE'],inplace=True)

In [17]:
admid_icd['icd_div']=admid_icd.ICD9_CODE.apply(category)

In [18]:
admid_icd

ROW_ID  SUBJECT_ID  HADM_ID  SEQ_NUM ICD9_CODE    icd_div
0         1297         109   172335      1.0     40301  [403, 01]
1         1298         109   172335      2.0       486    [486, ]
2         1299         109   172335      3.0     58281  [582, 81]
3         1300         109   172335      4.0      5855   [585, 5]
4         1301         109   172335      5.0      4254   [425, 4]
...        ...         ...      ...      ...       ...        ...
651042  639798       97503   188195      2.0     20280  [202, 80]
651043  639799       97503   188195      3.0     V5869  [V58, 69]
651044  639800       97503   188195      4.0     V1279  [V12, 79]
651045  639801       97503   188195      5.0      5275   [527, 5]
651046  639802       97503   188195      6.0      5569   [556, 9]

[651000 rows x 6 columns]

In [19]:
admid_icd[['icd_cat','icd_spec']]=admid_icd.icd_div.apply(pd.Series)

In [20]:
admid_icd_cat=admid_icd.groupby('HADM_ID').agg({'icd_cat':lambda x: ','.join(x)}).reset_index()

In [21]:
admid_icd_cat

HADM_ID  \
0       100001   
1       100003   
2       100006   
3       100007   
4       100009   
...        ...   
58924   199993   
58925   199994   
58926   199995   
58927   199998   
58928   199999   

                                                                       icd_cat  
0              250,337,584,578,V58,250,536,458,250,403,585,250,362,250,707,V13  
1                                          531,285,070,571,456,537,401,535,782  
2                                          493,518,486,203,276,785,309,V12,V15  
3                                                          560,557,997,486,401  
4      414,996,414,250,278,V85,414,411,V45,V15,285,401,272,426,440,V15,V58,V45  
...                                                                        ...  
58924                                      410,428,427,427,518,424,276,511,518  
58925                                      486,428,518,397,496,416,585,427,276  
58926                                  421,746,429,304,441,442,V12,041,305,305  
58927          414,997,997,427,788,411,V45,E87,429,440,401,443,272,518,272,V45  
58928                      482,518,511,584,276,786,799,414,V45,788,285,V49,429  

[58929 rows x 2 columns]

In [22]:
admid_icd_cat['icd_cat']=admid_icd_cat.icd_cat.apply(spliticdstring)

In [23]:
admid_icd_cat

HADM_ID  \
0       100001   
1       100003   
2       100006   
3       100007   
4       100009   
...        ...   
58924   199993   
58925   199994   
58926   199995   
58927   199998   
58928   199999   

                                                                      icd_cat  
0                [403, 536, V58, 578, 584, 707, 250, V13, 337, 458, 362, 585]  
1                               [537, 456, 401, 531, 535, 571, 782, 070, 285]  
2                               [785, 203, V15, 276, 486, 309, 493, V12, 518]  
3                                                   [560, 557, 486, 997, 401]  
4      [411, 426, V58, V15, 272, 414, 250, V45, 278, 401, 285, 996, 440, V85]  
...                                                                       ...  
58924                                     [511, 276, 428, 427, 410, 424, 518]  
58925                           [276, 486, 428, 427, 397, 416, 518, 496, 585]  
58926                           [441, 041, 746, 305, 421, 429, V12, 442, 304]  
58927       [411, 443, 518, 272, 414, 427, V45, 997, 429, 401, 788, 440, E87]  
58928       [786, 511, 482, 584, 276, 414, V45, 799, 429, 518, 788, V49, 285]  

[58929 rows x 2 columns]

In [24]:
icdcat=admid_icd_cat.icd_cat.to_list()
icdcat

[['403',
  '536',
  'V58',
  '578',
  '584',
  '707',
  '250',
  'V13',
  '337',
  '458',
  '362',
  '585'],
 ['537', '456', '401', '531', '535', '571', '782', '070', '285'],
 ['785', '203', 'V15', '276', '486', '309', '493', 'V12', '518'],
 ['560', '557', '486', '997', '401'],
 ['411',
  '426',
  'V58',
  'V15',
  '272',
  '414',
  '250',
  'V45',
  '278',
  '401',
  '285',
  '996',
  '440',
  'V85'],
 ['198', '276', '196', '197', '189'],
 ['852',
  '825',
  '482',
  '822',
  '805',
  '305',
  '807',
  '890',
  '864',
  '821',
  'E81',
  '860',
  '861',
  '285'],
 ['V10', 'V87', '272', 'V15', '414', 'V45', '998', '401', 'E87', '413'],
 ['300', '718', '738', 'V45', '278', '726'],
 ['345', '251', '300', '536', '507', '758', '478', '458', '518', '255', 'V44'],
 ['296', '301', 'E95', '780', '276', '518', '969', '304'],
 ['536',
  '225',
  '250',
  'V45',
  '278',
  '432',
  '496',
  '443',
  '511',
  '707',
  '428',
  '682',
  '357',
  '585',
  '403',
  'V58',
  'V62',
  '746',
  '722',
 

In [25]:
t_icdcat=[a for b in icdcat for a in b]

In [26]:
icdcat_dict=dict(Counter(t_icdcat))
icdcat_dict=dict(sorted(icdcat_dict.items(),key= lambda x: x[1],reverse=True))

In [27]:
icdcat_dict

{'401': 21305,
 '427': 17226,
 '276': 15101,
 '272': 14558,
 '414': 14410,
 '250': 14222,
 '428': 13608,
 '518': 13346,
 '285': 12606,
 '584': 11422,
 'V45': 9132,
 '530': 7392,
 '599': 7329,
 'V58': 7162,
 '585': 6918,
 'E87': 6654,
 '403': 6438,
 'V10': 6410,
 'V30': 6340,
 '038': 6265,
 'V05': 5790,
 'V29': 5735,
 '995': 5642,
 '424': 5488,
 '780': 5449,
 '410': 5430,
 '785': 5351,
 '244': 5237,
 '305': 5213,
 '997': 5158,
 '998': 5055,
 '458': 5045,
 '486': 4838,
 'V15': 4530,
 '041': 4449,
 '496': 4431,
 '996': 4356,
 '287': 3960,
 'V12': 3886,
 '790': 3730,
 '507': 3696,
 'E93': 3518,
 '493': 3515,
 '311': 3431,
 '765': 3430,
 '412': 3278,
 '511': 3268,
 '348': 3261,
 '707': 3186,
 'E88': 3075,
 '571': 2951,
 '774': 2928,
 '300': 2924,
 '733': 2799,
 '770': 2775,
 '278': 2715,
 '416': 2674,
 '070': 2553,
 '578': 2451,
 '787': 2408,
 '327': 2402,
 '274': 2346,
 '482': 2222,
 'V49': 2211,
 'V43': 2195,
 '280': 2183,
 '303': 2109,
 '425': 2106,
 'E84': 2072,
 '286': 2028,
 'V50': 20

In [29]:
discharge_icd

SUBJECT_ID   HADM_ID           CATEGORY DESCRIPTION  ISERROR  \
0           22532  167853.0  Discharge summary      Report      NaN   
1           13702  107527.0  Discharge summary      Report      NaN   
2           13702  167118.0  Discharge summary      Report      NaN   
3           13702  196489.0  Discharge summary      Report      NaN   
4           26880  135453.0  Discharge summary      Report      NaN   
...           ...       ...                ...         ...      ...   
59647       93924  135672.0  Discharge summary    Addendum      NaN   
59648       17782  155710.0  Discharge summary    Addendum      NaN   
59649       96333  183951.0  Discharge summary    Addendum      NaN   
59650       66717  169165.0  Discharge summary    Addendum      NaN   
59651       73790  157100.0  Discharge summary    Addendum      NaN   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

In [30]:
discharge_icd.HADM_ID.nunique()

52726

In [31]:
discharge_icd[discharge_icd.ICD9_CODE_x.isna()].count()

SUBJECT_ID                6
HADM_ID                   6
CATEGORY                  6
DESCRIPTION               6
ISERROR                   0
TEXT                      6
text_mod                  6
sec                       6
split                     6
service:                  6
social history:           4
family history:           4
past medical history:     4
chief complaint:          5
discharge medications:    2
discharge disposition:    6
discharge diagnosis:      5
allergies:                6
physical exam:            4
ICD9_CODE_x               0
ICD10                     0
ICD9_CODE_y               0
icd10_pcs                 0
dtype: int64

In [32]:
discharge_icd.dropna(subset=['ICD9_CODE_x'],inplace=True)

In [33]:
discharge_icd['icd9_codes']=discharge_icd.ICD9_CODE_x.apply(spliticdstring)

In [34]:
discharge_icd

SUBJECT_ID   HADM_ID           CATEGORY DESCRIPTION  ISERROR  \
0           22532  167853.0  Discharge summary      Report      NaN   
1           13702  107527.0  Discharge summary      Report      NaN   
2           13702  167118.0  Discharge summary      Report      NaN   
3           13702  196489.0  Discharge summary      Report      NaN   
4           26880  135453.0  Discharge summary      Report      NaN   
...           ...       ...                ...         ...      ...   
59647       93924  135672.0  Discharge summary    Addendum      NaN   
59648       17782  155710.0  Discharge summary    Addendum      NaN   
59649       96333  183951.0  Discharge summary    Addendum      NaN   
59650       66717  169165.0  Discharge summary    Addendum      NaN   
59651       73790  157100.0  Discharge summary    Addendum      NaN   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

In [35]:
def category_see(x):
    return list(set([re.split("(\d{3}|[VE]\d{2})",i)[1] for i in x]))
    

In [36]:
a=['4314','4317','V123']

In [37]:
category_see(a)

['V12', '431']

In [38]:
discharge_icd['icd9_cat']=discharge_icd.icd9_codes.apply(category_see)

In [220]:
discharge_icd

KeyboardInterrupt: 

In [40]:
discharge_icd_cat=discharge_icd.icd9_cat.to_list()
discharge_icd_cat

[['211', '511', '507', '276', '427', '011', '263', '425'],
 ['519', '276', '486', '491', '518', '311', '244'],
 ['453', '496', '519', '276', '518', '553'],
 ['519',
  '491',
  '359',
  '578',
  '530',
  '416',
  'V02',
  '401',
  '458',
  '348',
  '272',
  '584',
  '553',
  '487',
  '276',
  '414',
  '531',
  '518',
  'E93',
  '244'],
 ['453',
  '293',
  '507',
  '805',
  '428',
  '427',
  'V45',
  '401',
  'E88',
  '802',
  'V12',
  '788'],
 ['443', '710', '530', '225', 'V43', '714'],
 ['V58', '486', '428', '401', 'V45', '518', '577', '415'],
 ['V10', 'V58', '225', '427', 'V45', '401'],
 ['345', '348', '747', '437', '909'],
 ['345', '300', '530', '348', '738', '437', '278', '909'],
 ['507',
  '272',
  '584',
  '428',
  '414',
  '427',
  '250',
  'V45',
  '410',
  '599',
  '401',
  '440',
  'E87'],
 ['008',
  '403',
  'V10',
  '530',
  '276',
  '486',
  '578',
  '428',
  '427',
  '584',
  '112',
  '280',
  '263',
  '440',
  '287'],
 ['411', '365', '530', '414', '305', '401'],
 ['411', 

In [41]:
t_discharge_icd_cat=[a for b in discharge_icd_cat for a in b]
t_discharge_icd_cat

['211',
 '511',
 '507',
 '276',
 '427',
 '011',
 '263',
 '425',
 '519',
 '276',
 '486',
 '491',
 '518',
 '311',
 '244',
 '453',
 '496',
 '519',
 '276',
 '518',
 '553',
 '519',
 '491',
 '359',
 '578',
 '530',
 '416',
 'V02',
 '401',
 '458',
 '348',
 '272',
 '584',
 '553',
 '487',
 '276',
 '414',
 '531',
 '518',
 'E93',
 '244',
 '453',
 '293',
 '507',
 '805',
 '428',
 '427',
 'V45',
 '401',
 'E88',
 '802',
 'V12',
 '788',
 '443',
 '710',
 '530',
 '225',
 'V43',
 '714',
 'V58',
 '486',
 '428',
 '401',
 'V45',
 '518',
 '577',
 '415',
 'V10',
 'V58',
 '225',
 '427',
 'V45',
 '401',
 '345',
 '348',
 '747',
 '437',
 '909',
 '345',
 '300',
 '530',
 '348',
 '738',
 '437',
 '278',
 '909',
 '507',
 '272',
 '584',
 '428',
 '414',
 '427',
 '250',
 'V45',
 '410',
 '599',
 '401',
 '440',
 'E87',
 '008',
 '403',
 'V10',
 '530',
 '276',
 '486',
 '578',
 '428',
 '427',
 '584',
 '112',
 '280',
 '263',
 '440',
 '287',
 '411',
 '365',
 '530',
 '414',
 '305',
 '401',
 '411',
 '365',
 '530',
 '414',
 '305',


In [42]:
discharge_icd_cat_dict=dict(Counter(t_discharge_icd_cat))
discharge_icd_cat_dict=dict(sorted(discharge_icd_cat_dict.items(),key= lambda x: x[1],reverse=True))


In [43]:
discharge_icd_cat_dict

{'401': 23030,
 '427': 19185,
 '276': 16507,
 '414': 15894,
 '272': 15694,
 '250': 15582,
 '428': 15499,
 '518': 14979,
 '285': 13769,
 '584': 12579,
 'V45': 9728,
 '599': 8367,
 '530': 7874,
 'V58': 7667,
 '585': 7318,
 'E87': 7201,
 '038': 6968,
 '403': 6930,
 'V10': 6810,
 '424': 6242,
 '410': 6183,
 '780': 6011,
 '997': 5942,
 '995': 5921,
 '998': 5800,
 '244': 5624,
 '785': 5598,
 '305': 5510,
 '458': 5505,
 '486': 5356,
 '996': 5066,
 '041': 4943,
 '496': 4917,
 'V15': 4793,
 '287': 4361,
 '507': 4273,
 '790': 4161,
 'V12': 4109,
 'E93': 3804,
 '511': 3743,
 '493': 3714,
 '707': 3677,
 '311': 3669,
 '412': 3582,
 '348': 3425,
 '765': 3340,
 'E88': 3276,
 '571': 3160,
 '300': 3111,
 '733': 2987,
 '278': 2966,
 '416': 2953,
 '774': 2867,
 'V29': 2762,
 '070': 2720,
 '578': 2665,
 '482': 2660,
 '770': 2605,
 'V30': 2599,
 '787': 2577,
 '327': 2527,
 '274': 2495,
 '280': 2420,
 'V43': 2357,
 '425': 2340,
 'V05': 2305,
 'V49': 2276,
 '303': 2217,
 '788': 2216,
 '411': 2203,
 '286': 21

In [44]:
def relatedcategories(x):
    icdcodeswith_x=discharge_icd[discharge_icd.icd9_cat.apply(lambda y: x in y)].icd9_cat.tolist()
    total_icdcodeswithx=[a for b in icdcodeswith_x for a in b]
    dictcodeswith_x=dict(Counter(total_icdcodeswithx))
    dictcodeswith_x=dict(sorted(dictcodeswith_x.items(),key= lambda x: x[1],reverse=True))
    value=dictcodeswith_x[x]
    del dictcodeswith_x[x]
    count_cat={'category':[i for i in dictcodeswith_x],
           'No. of times with category'+' '+x+'(in %)':[dictcodeswith_x[i] for i in dictcodeswith_x]}
    count_cat_table=pd.DataFrame.from_dict(count_cat)
    count_cat_table['No. of times with category'+' '+x+'(in %)']=count_cat_table['No. of times with category'+' '+x+'(in %)'].apply(lambda x : x/value*100)
    return value,count_cat_table.head(5)

In [45]:
relatedcategories('401')

(23030,
   category  No. of times with category 401(in %)
 0      272                             43.660443
 1      414                             37.138515
 2      427                             37.025619
 3      250                             32.409900
 4      276                             26.726010)

In [46]:
relatedcategories('427')

(19185,
   category  No. of times with category 427(in %)
 0      401                             44.446182
 1      428                             43.810268
 2      414                             38.743810
 3      272                             32.718269
 4      276                             32.019807)

In [47]:
relatedcategories('276')

(16507,
   category  No. of times with category 276(in %)
 0      584                             41.782274
 1      518                             38.456412
 2      401                             37.287211
 3      427                             37.214515
 4      285                             33.452475)

In [48]:
relatedcategories('414')

(15894,
   category  No. of times with category 414(in %)
 0      401                             53.812760
 1      272                             49.559582
 2      427                             46.766075
 3      428                             41.380395
 4      250                             39.700516)

In [49]:
relatedcategories('272')

(15694,
   category  No. of times with category 272(in %)
 0      401                             64.069071
 1      414                             50.191156
 2      427                             39.996177
 3      250                             38.224799
 4      428                             29.036574)

In [50]:
relatedcategories('250')

(15582,
   category  No. of times with category 250(in %)
 0      401                             47.901425
 1      414                             40.495443
 2      428                             38.769093
 3      272                             38.499551
 4      427                             36.792453)

In [51]:
relatedcategories('428')

(15499,
   category  No. of times with category 428(in %)
 0      427                             54.229305
 1      414                             42.434996
 2      250                             38.976708
 3      401                             36.441061
 4      584                             36.279760)

In [52]:
relatedcategories('518')

(14979,
   category  No. of times with category 518(in %)
 0      276                             42.379331
 1      427                             39.461913
 2      401                             36.404299
 3      428                             35.896922
 4      584                             35.135857)

In [53]:
relatedcategories('285')

(13769,
   category  No. of times with category 285(in %)
 0      276                             40.104583
 1      401                             39.029704
 2      427                             36.858160
 3      250                             32.740214
 4      428                             31.912267)

In [54]:
relatedcategories('584')

(12579,
   category  No. of times with category 584(in %)
 0      276                             54.829478
 1      428                             44.701487
 2      427                             42.078067
 3      518                             41.839574
 4      250                             36.656332)

In [55]:
discharge_icd.fillna('',inplace=True)

In [56]:
discharge_icd[discharge_icd.icd9_cat.apply(lambda x: '401' in x)& ~(discharge_icd['discharge diagnosis:'].str.contains("hypertension"))][['HADM_ID','discharge diagnosis:','icd9_cat']]

HADM_ID  \
4      135453.0   
6      134727.0   
7      114236.0   
12     169684.0   
13     169684.0   
...         ...   
59645  112538.0   
59647  135672.0   
59648  155710.0   
59649  183951.0   
59650  169165.0   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               discharge diagnosis:  \
4                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           

In [57]:
discharge_icd[discharge_icd.text_mod.str.contains("diabetes")]

SUBJECT_ID   HADM_ID           CATEGORY DESCRIPTION ISERROR  \
5           53181  170490.0  Discharge summary      Report           
10          28063  121936.0  Discharge summary      Report           
16          10044  124073.0  Discharge summary      Report           
19           9805  188132.0  Discharge summary      Report           
20           9805  177212.0  Discharge summary      Report           
...           ...       ...                ...         ...     ...   
59612       82943  127716.0  Discharge summary    Addendum           
59615       92764  186377.0  Discharge summary    Addendum           
59621       92346  156564.0  Discharge summary    Addendum           
59642       49879  114661.0  Discharge summary    Addendum           
59647       93924  135672.0  Discharge summary    Addendum           

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

In [58]:
discharge_icd.columns

Index(['SUBJECT_ID', 'HADM_ID', 'CATEGORY', 'DESCRIPTION', 'ISERROR', 'TEXT',
       'text_mod', 'sec', 'split', 'service:', 'social history:',
       'family history:', 'past medical history:', 'chief complaint:',
       'discharge medications:', 'discharge disposition:',
       'discharge diagnosis:', 'allergies:', 'physical exam:', 'ICD9_CODE_x',
       'ICD10', 'ICD9_CODE_y', 'icd10_pcs', 'icd9_codes', 'icd9_cat'],
      dtype='object')

In [59]:
#nlp=spacy.load('en_core_sci_md')

In [60]:
nlp=spacy.load('en_ner_bc5cdr_md')

In [61]:
discharge_icd

SUBJECT_ID   HADM_ID           CATEGORY DESCRIPTION ISERROR  \
0           22532  167853.0  Discharge summary      Report           
1           13702  107527.0  Discharge summary      Report           
2           13702  167118.0  Discharge summary      Report           
3           13702  196489.0  Discharge summary      Report           
4           26880  135453.0  Discharge summary      Report           
...           ...       ...                ...         ...     ...   
59647       93924  135672.0  Discharge summary    Addendum           
59648       17782  155710.0  Discharge summary    Addendum           
59649       96333  183951.0  Discharge summary    Addendum           
59650       66717  169165.0  Discharge summary    Addendum           
59651       73790  157100.0  Discharge summary    Addendum           

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

In [62]:
diagnosis=discharge_icd[['HADM_ID','discharge diagnosis:','icd9_cat']]

In [63]:
diagnosis['discharge diagnosis:'].fillna('',inplace=True)

c:\users\hp\appdata\local\programs\python\python38\lib\site-packages\pandas\core\generic.py:6245: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._update_inplace(new_data)


In [64]:
diagnosis

HADM_ID  \
0      167853.0   
1      107527.0   
2      167118.0   
3      196489.0   
4      135453.0   
...         ...   
59647  135672.0   
59648  155710.0   
59649  183951.0   
59650  169165.0   
59651  157100.0   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    discharge diagnosis:  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      

In [97]:
from tqdm._tqdm_notebook import tqdm_notebook

tqdm_notebook.pandas()

<ipython-input-97-282d983cd844>:1: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.*` instead of `tqdm._tqdm_notebook.*`
  from tqdm._tqdm_notebook import tqdm_notebook
c:\users\hp\appdata\local\programs\python\python38\lib\site-packages\tqdm\std.py:668: FutureWarning: The Panel class is removed from pandas. Accessing it from the top-level namespace will also be removed in the next version
  from pandas import Panel


In [98]:
%%time
diagnosis['medical_term']=diagnosis['discharge diagnosis:'].progress_apply(lambda x:nlp(x).ents)


Wall time: 2h 30min 50s


<timed exec>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [66]:
discharge_icd.columns

Index(['SUBJECT_ID', 'HADM_ID', 'CATEGORY', 'DESCRIPTION', 'ISERROR', 'TEXT',
       'text_mod', 'sec', 'split', 'service:', 'social history:',
       'family history:', 'past medical history:', 'chief complaint:',
       'discharge medications:', 'discharge disposition:',
       'discharge diagnosis:', 'allergies:', 'physical exam:', 'ICD9_CODE_x',
       'ICD10', 'ICD9_CODE_y', 'icd10_pcs', 'icd9_codes', 'icd9_cat'],
      dtype='object')

In [100]:
text=discharge_icd['discharge diagnosis:'].iloc[2]

In [128]:
y=nlp(text).ents

In [102]:
y

(coronary artery disease/atypical angina,
 hypercholesterolemia,
 hypothyroidism,
 hypertension,
 cerebral vascular accident,
 head injury,
 fracture,
 chest pain,
 cough)

In [78]:
y[1]

tingling

In [99]:
diagnosis

HADM_ID  \
0      167853.0   
1      107527.0   
2      167118.0   
3      196489.0   
4      135453.0   
...         ...   
59647  135672.0   
59648  155710.0   
59649  183951.0   
59650  169165.0   
59651  157100.0   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    discharge diagnosis:  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      

In [132]:
y=diagnosis.medical_term.apply(lambda x: list(x)).to_list()

In [133]:
y

[[],
 [],
 [coronary artery disease/atypical angina,
  hypercholesterolemia,
  hypothyroidism,
  hypertension,
  cerebral vascular accident,
  head injury,
  fracture,
  chest pain,
  cough],
 [chronic obstructive pulmonary disease,
  respiratory failure,
  gastrointestinal bleed/peptic ulcer,
  hypertension,
  anxiety,
  coronary artery disease,
  hypothyroidism,
  shortness of breath,
  lethargy,
  steroids,
  inflammation,
  oxygen,
  steroid,
  shortness of breath,
  chest pain,
  pantoprazole,
  omeprazole  ,
  hydrochlorothiazide  ,
  prednisone,
  senna,
  constipation,
  morphine,
  respiratory discomfort,
  furosemide  ,
  zolpidem  ,
  aspirin  ,
  trazodone],
 [spondylosis,
  calcification of posterior,
  fracture dislocation,
  pneumonia,
  cervical spondylosis,
  calcification of posterior      longitudinal ligament,
  fracture dislocation,
  pneumonia,
  spondylosis,
  calcification of posterior      longitudinal ligament,
  fracture dislocation,
  pneumonia,
  urinary re

In [134]:
y1=[[a.text for a in i] for i in y]

In [135]:
y1

[[],
 [],
 ['coronary artery disease/atypical angina',
  'hypercholesterolemia',
  'hypothyroidism',
  'hypertension',
  'cerebral vascular accident',
  'head injury',
  'fracture',
  'chest pain',
  'cough'],
 ['chronic obstructive pulmonary disease',
  'respiratory failure',
  'gastrointestinal bleed/peptic ulcer',
  'hypertension',
  'anxiety',
  'coronary artery disease',
  'hypothyroidism',
  'shortness of breath',
  'lethargy',
  'steroids',
  'inflammation',
  'oxygen',
  'steroid',
  'shortness of breath',
  'chest pain',
  'pantoprazole',
  'omeprazole  ',
  'hydrochlorothiazide  ',
  'prednisone',
  'senna',
  'constipation',
  'morphine',
  'respiratory discomfort',
  'furosemide  ',
  'zolpidem  ',
  'aspirin  ',
  'trazodone'],
 ['spondylosis',
  'calcification of posterior',
  'fracture dislocation',
  'pneumonia',
  'cervical spondylosis',
  'calcification of posterior      longitudinal ligament',
  'fracture dislocation',
  'pneumonia',
  'spondylosis',
  'calcification

In [138]:
z=[list(set(i)) for i in y1]

In [139]:
z

[[],
 [],
 ['hypercholesterolemia',
  'cerebral vascular accident',
  'coronary artery disease/atypical angina',
  'chest pain',
  'cough',
  'hypothyroidism',
  'head injury',
  'hypertension',
  'fracture'],
 ['trazodone',
  'zolpidem  ',
  'chest pain',
  'coronary artery disease',
  'oxygen',
  'hypertension',
  'prednisone',
  'pantoprazole',
  'inflammation',
  'anxiety',
  'furosemide  ',
  'aspirin  ',
  'omeprazole  ',
  'senna',
  'steroid',
  'respiratory discomfort',
  'respiratory failure',
  'morphine',
  'hypothyroidism',
  'lethargy',
  'gastrointestinal bleed/peptic ulcer',
  'hydrochlorothiazide  ',
  'steroids',
  'chronic obstructive pulmonary disease',
  'shortness of breath',
  'constipation'],
 ['calcification of posterior',
  'olanzapine',
  'calcification of posterior      longitudinal ligament',
  'pneumonia',
  'fracture dislocation',
  'spondylosis',
  'cervical spondylosis',
  'morphine  ',
  'urinary retention',
  'pain'],
 ['phenytoin',
  'tingling',
  'n

In [140]:
diagnosis_x=diagnosis[diagnosis.icd9_cat.apply(lambda x: '401' in x)]

In [141]:
diagnosis_x

HADM_ID  \
3      196489.0   
4      135453.0   
6      134727.0   
7      114236.0   
10     121936.0   
...         ...   
59645  112538.0   
59647  135672.0   
59648  155710.0   
59649  183951.0   
59650  169165.0   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    discharge diagnosis:  \
3      discharge diagnosis:  primary:  1. chronic obstructive pulmonary disease exacerbation  2. respiratory failure with intubation  3. upper gastrointestinal bleed/peptic ulcer disease  4. hypertension  5. anxiety    secondary:  1. coronary artery disease  2. hypothyroidism      discharge condition:  mental status: confused - sometimes.  level of consciousness: alert and interactive.  activity status: out of bed with assistance to chair or  wheelchair.      discharge instructions:  you were admitted to the hospital with shortness of breath and  respiratory failure and lethargy. in the emergency department,  you were breathing very fast and a breathing tube was inserted  into your airway to help you breathe. you were admitted to the  intensive care unit. there, you were managed with steroids and  antibiotics and the tube was eventually removed from your  airway, allowing you to breathe on your own. you also underwent  bronchoscopy which looked at the inside of your ai

In [142]:
y=diagnosis_x.medical_term.apply(lambda x: list(x)).to_list()
y1=[[a.text for a in i] for i in y]
z=[list(set(i)) for i in y1]

In [143]:
z

[['trazodone',
  'zolpidem  ',
  'chest pain',
  'coronary artery disease',
  'oxygen',
  'hypertension',
  'prednisone',
  'pantoprazole',
  'inflammation',
  'anxiety',
  'furosemide  ',
  'aspirin  ',
  'omeprazole  ',
  'senna',
  'steroid',
  'respiratory discomfort',
  'respiratory failure',
  'morphine',
  'hypothyroidism',
  'lethargy',
  'gastrointestinal bleed/peptic ulcer',
  'hydrochlorothiazide  ',
  'steroids',
  'chronic obstructive pulmonary disease',
  'shortness of breath',
  'constipation'],
 ['calcification of posterior',
  'olanzapine',
  'calcification of posterior      longitudinal ligament',
  'pneumonia',
  'fracture dislocation',
  'spondylosis',
  'cervical spondylosis',
  'morphine  ',
  'urinary retention',
  'pain'],
 [],
 ['confusion',
  'steroid',
  'fever',
  'tingling',
  'docusate',
  'weakness',
  'numbness',
  'tremors',
  'headache',
  'tenderness',
  'motrin',
  'infection',
  'aspirin',
  'levetiracetam',
  'seizures',
  'redness',
  'pain',
  'c

In [145]:
z1=[a for b in z for a in b]

In [146]:
z1

['trazodone',
 'zolpidem  ',
 'chest pain',
 'coronary artery disease',
 'oxygen',
 'hypertension',
 'prednisone',
 'pantoprazole',
 'inflammation',
 'anxiety',
 'furosemide  ',
 'aspirin  ',
 'omeprazole  ',
 'senna',
 'steroid',
 'respiratory discomfort',
 'respiratory failure',
 'morphine',
 'hypothyroidism',
 'lethargy',
 'gastrointestinal bleed/peptic ulcer',
 'hydrochlorothiazide  ',
 'steroids',
 'chronic obstructive pulmonary disease',
 'shortness of breath',
 'constipation',
 'calcification of posterior',
 'olanzapine',
 'calcification of posterior      longitudinal ligament',
 'pneumonia',
 'fracture dislocation',
 'spondylosis',
 'cervical spondylosis',
 'morphine  ',
 'urinary retention',
 'pain',
 'confusion',
 'steroid',
 'fever',
 'tingling',
 'docusate',
 'weakness',
 'numbness',
 'tremors',
 'headache',
 'tenderness',
 'motrin',
 'infection',
 'aspirin',
 'levetiracetam',
 'seizures',
 'redness',
 'pain',
 'constipation',
 'atrial fibrillation',
 'diabetes mellitus',
 

In [147]:
dict_med=dict(Counter(z1))

In [148]:
dict_med

{'trazodone': 43,
 'zolpidem  ': 2,
 'chest pain': 3432,
 'coronary artery disease': 382,
 'oxygen': 641,
 'hypertension': 2210,
 'prednisone': 421,
 'pantoprazole': 193,
 'inflammation': 108,
 'anxiety': 260,
 'furosemide  ': 16,
 'aspirin  ': 103,
 'omeprazole  ': 24,
 'senna': 108,
 'steroid': 206,
 'respiratory discomfort': 1,
 'respiratory failure': 327,
 'morphine': 108,
 'hypothyroidism': 242,
 'lethargy': 187,
 'gastrointestinal bleed/peptic ulcer': 1,
 'hydrochlorothiazide  ': 34,
 'steroids': 299,
 'chronic obstructive pulmonary disease': 70,
 'shortness of breath': 2831,
 'constipation': 1468,
 'calcification of posterior': 1,
 'olanzapine': 14,
 'calcification of posterior      longitudinal ligament': 1,
 'pneumonia': 1603,
 'fracture dislocation': 4,
 'spondylosis': 15,
 'cervical spondylosis': 8,
 'morphine  ': 8,
 'urinary retention': 54,
 'pain': 4808,
 'confusion': 1010,
 'fever': 3750,
 'tingling': 621,
 'docusate': 576,
 'weakness': 1042,
 'numbness': 984,
 'tremors'

In [149]:
dict_med=dict(sorted(dict_med.items(),key= lambda x: x[1],reverse=True))

In [150]:
dict_med

{'pain': 4808,
 'fever': 3750,
 'phone:<telephone': 3652,
 'chest pain': 3432,
 'shortness of breath': 2831,
 'redness': 2345,
 'aspirin': 2307,
 'hypertension': 2210,
 'infection': 2194,
 'chills': 2069,
 'atrial fibrillation': 2025,
 'bleeding': 1752,
 'coumadin': 1745,
 'pneumonia': 1603,
 'vomiting': 1544,
 'fevers': 1522,
 'constipation': 1468,
 'swelling': 1304,
 'nausea': 1293,
 'erythema': 1089,
 'cough': 1068,
 'weakness': 1042,
 'headache': 1041,
 'abdominal pain': 1031,
 'confusion': 1010,
 'numbness': 984,
 'diarrhea': 923,
 'weight gain': 913,
 'lisinopril': 845,
 'seizures': 812,
 'metoprolol': 790,
 'motrin': 742,
 'myocardial infarction': 720,
 'anemia': 688,
 'stroke': 667,
 'monday': 661,
 'oxygen': 641,
 'alcohol': 627,
 'tingling': 621,
 'tylenol': 605,
 'dizziness': 602,
 'dehydration': 602,
 'mouth': 589,
 'sodium': 583,
 'docusate': 576,
 'vomit': 568,
 'diabetes mellitus': 558,
 'fracture': 541,
 'tremors': 536,
 'diabetes': 533,
 'urinary tract infection': 494,

In [160]:
dict_med_list=list(dict_med)

In [161]:
dict_med_list

['pain',
 'fever',
 'phone:<telephone',
 'chest pain',
 'shortness of breath',
 'redness',
 'aspirin',
 'hypertension',
 'infection',
 'chills',
 'atrial fibrillation',
 'bleeding',
 'coumadin',
 'pneumonia',
 'vomiting',
 'fevers',
 'constipation',
 'swelling',
 'nausea',
 'erythema',
 'cough',
 'weakness',
 'headache',
 'abdominal pain',
 'confusion',
 'numbness',
 'diarrhea',
 'weight gain',
 'lisinopril',
 'seizures',
 'metoprolol',
 'motrin',
 'myocardial infarction',
 'anemia',
 'stroke',
 'monday',
 'oxygen',
 'alcohol',
 'tingling',
 'tylenol',
 'dizziness',
 'dehydration',
 'mouth',
 'sodium',
 'docusate',
 'vomit',
 'diabetes mellitus',
 'fracture',
 'tremors',
 'diabetes',
 'urinary tract infection',
 'warfarin',
 'bleed',
 'hyperlipidemia',
 'shortness',
 'heart failure',
 'cholesterol',
 'prednisone',
 'seizure',
 'coronary artery disease',
 'hematoma',
 'blood loss anemia',
 'ibuprofen',
 'edema',
 'wheezing',
 'oxycodone',
 'respiratory failure',
 'infectious disease',
 

In [162]:
dict_med_list=[i for i in dict_med_list if i!='phone:<telephone']

In [163]:
dict_med_list

['pain',
 'fever',
 'chest pain',
 'shortness of breath',
 'redness',
 'aspirin',
 'hypertension',
 'infection',
 'chills',
 'atrial fibrillation',
 'bleeding',
 'coumadin',
 'pneumonia',
 'vomiting',
 'fevers',
 'constipation',
 'swelling',
 'nausea',
 'erythema',
 'cough',
 'weakness',
 'headache',
 'abdominal pain',
 'confusion',
 'numbness',
 'diarrhea',
 'weight gain',
 'lisinopril',
 'seizures',
 'metoprolol',
 'motrin',
 'myocardial infarction',
 'anemia',
 'stroke',
 'monday',
 'oxygen',
 'alcohol',
 'tingling',
 'tylenol',
 'dizziness',
 'dehydration',
 'mouth',
 'sodium',
 'docusate',
 'vomit',
 'diabetes mellitus',
 'fracture',
 'tremors',
 'diabetes',
 'urinary tract infection',
 'warfarin',
 'bleed',
 'hyperlipidemia',
 'shortness',
 'heart failure',
 'cholesterol',
 'prednisone',
 'seizure',
 'coronary artery disease',
 'hematoma',
 'blood loss anemia',
 'ibuprofen',
 'edema',
 'wheezing',
 'oxycodone',
 'respiratory failure',
 'infectious disease',
 'dry mouth',
 'hyperc

In [167]:
frequent_cat=['401','427','276','414','272','250','428','518','285','584']
category_terms={}
for i in frequent_cat:
    diagnosis_x=diagnosis[diagnosis.icd9_cat.apply(lambda x: i in x)]
    y=diagnosis_x.medical_term.apply(lambda x: list(x)).to_list()
    y1=[[a.text for a in b] for b in y]
    z=[list(set(a)) for a in y1]
    z1=[a for b in z for a in b]
    dict_med=dict(Counter(z1))
    dict_med=dict(sorted(dict_med.items(),key= lambda x: x[1],reverse=True))
    dict_med_list=list(dict_med)
    dict_med_list=[a for a in dict_med_list if a!='phone:<telephone']
    category_terms[i]=dict_med_list[:10]

In [168]:
category_terms

{'401': ['pain',
  'fever',
  'chest pain',
  'shortness of breath',
  'redness',
  'aspirin',
  'hypertension',
  'infection',
  'chills',
  'atrial fibrillation'],
 '427': ['atrial fibrillation',
  'pain',
  'chest pain',
  'fever',
  'coumadin',
  'shortness of breath',
  'infection',
  'pneumonia',
  'redness',
  'chills'],
 '276': ['pain',
  'chest pain',
  'shortness of breath',
  'fever',
  'pneumonia',
  'chills',
  'infection',
  'fevers',
  'atrial fibrillation',
  'vomiting'],
 '414': ['pain',
  'chest pain',
  'fever',
  'shortness of breath',
  'redness',
  'atrial fibrillation',
  'aspirin',
  'infection',
  'coumadin',
  'hypertension'],
 '272': ['pain',
  'fever',
  'chest pain',
  'shortness of breath',
  'redness',
  'aspirin',
  'infection',
  'atrial fibrillation',
  'coumadin',
  'hypertension'],
 '250': ['pain',
  'chest pain',
  'fever',
  'shortness of breath',
  'chills',
  'infection',
  'atrial fibrillation',
  'hypertension',
  'fevers',
  'aspirin'],
 '428'

In [169]:
category_terms_table=pd.DataFrame.from_dict(category_terms)

In [172]:
category_terms_table=category_terms_table.T

In [174]:
category_terms_table.reset_index(level=0,inplace=True)

In [175]:
category_terms_table

index                    0                    1                    2  \
0   401                 pain                fever           chest pain   
1   427  atrial fibrillation                 pain           chest pain   
2   276                 pain           chest pain  shortness of breath   
3   414                 pain           chest pain                fever   
4   272                 pain                fever           chest pain   
5   250                 pain           chest pain                fever   
6   428           chest pain  shortness of breath  atrial fibrillation   
7   518                 pain  shortness of breath            pneumonia   
8   285                 pain           chest pain  shortness of breath   
9   584           chest pain  shortness of breath                 pain   

                     3          4                    5                    6  \
0  shortness of breath    redness              aspirin         hypertension   
1                fever   coumadin  shortness of breath            infection   
2                fever  pneumonia               chills            infection   
3  shortness of breath    redness  atrial fibrillation              aspirin   
4  shortness of breath    redness              aspirin            infection   
5  shortness of breath     chills            infection  atrial fibrillation   
6                 pain      fever            pneumonia             coumadin   
7           chest pain      fever               chills  atrial fibrillation   
8                fever   bleeding               chills            infection   
9                fever  pneumonia               chills  atrial fibrillation   

                     7                    8                    9  
0            infection               chills  atrial fibrillation  
1            pneumonia              redness               chills  
2               fevers  atrial fibrillation             vomiting  
3            infection             coumadin         hypertension  
4  atrial fibrillation             coumadin         hypertension  
5         hypertension               fevers              aspirin  
6               chills               fevers        heart failure  
7               fevers            infection             vomiting  
8            pneumonia               fevers  atrial fibrillation  
9               fevers            infection             vomiting

In [176]:
category_terms_table['med_terms'] = category_terms_table[category_terms_table.columns[1:]].apply(
    lambda x: ','.join(x.dropna().astype(str)),
    axis=1
)

In [177]:
category_terms_table

index                    0                    1                    2  \
0   401                 pain                fever           chest pain   
1   427  atrial fibrillation                 pain           chest pain   
2   276                 pain           chest pain  shortness of breath   
3   414                 pain           chest pain                fever   
4   272                 pain                fever           chest pain   
5   250                 pain           chest pain                fever   
6   428           chest pain  shortness of breath  atrial fibrillation   
7   518                 pain  shortness of breath            pneumonia   
8   285                 pain           chest pain  shortness of breath   
9   584           chest pain  shortness of breath                 pain   

                     3          4                    5                    6  \
0  shortness of breath    redness              aspirin         hypertension   
1                fever   coumadin  shortness of breath            infection   
2                fever  pneumonia               chills            infection   
3  shortness of breath    redness  atrial fibrillation              aspirin   
4  shortness of breath    redness              aspirin            infection   
5  shortness of breath     chills            infection  atrial fibrillation   
6                 pain      fever            pneumonia             coumadin   
7           chest pain      fever               chills  atrial fibrillation   
8                fever   bleeding               chills            infection   
9                fever  pneumonia               chills  atrial fibrillation   

                     7                    8                    9  \
0            infection               chills  atrial fibrillation   
1            pneumonia              redness               chills   
2               fevers  atrial fibrillation             vomiting   
3            infection             coumadin         hypertension   
4  atrial fibrillation             coumadin         hypertension   
5         hypertension               fevers              aspirin   
6               chills               fevers        heart failure   
7               fevers            infection             vomiting   
8            pneumonia               fevers  atrial fibrillation   
9               fevers            infection             vomiting   

                                                                                                       med_terms  
0    pain,fever,chest pain,shortness of breath,redness,aspirin,hypertension,infection,chills,atrial fibrillation  
1      atrial fibrillation,pain,chest pain,fever,coumadin,shortness of breath,infection,pneumonia,redness,chills  
2       pain,chest pain,shortness of breath,fever,pneumonia,chills,infection,fevers,atrial fibrillation,vomiting  
3  pain,chest pain,fever,shortness of breath,redness,atrial fibrillation,aspirin,infection,coumadin,hypertension  
4  pain,fever,chest pain,shortness of breath,redness,aspirin,infection,atrial fibrillation,coumadin,hypertension  
5     pain,chest pain,fever,shortness of breath,chills,infection,atrial fibrillation,hypertension,fevers,aspirin  
6   chest pain,shortness of breath,atrial fibrillation,pain,fever,pneumonia,coumadin,chills,fevers,heart failure  
7       pain,shortness of breath,pneumonia,chest pain,fever,chills,atrial fibrillation,fevers,infection,vomiting  
8       pain,chest pain,shortness of breath,fever,bleeding,chills,infection,pneumonia,fevers,atrial fibrillation  
9       chest pain,shortness of breath,pain,fever,pneumonia,chills,atrial fibrillation,fevers,infection,vomiting

In [178]:
category_terms_table[['index','med_terms']]

index  \
0   401   
1   427   
2   276   
3   414   
4   272   
5   250   
6   428   
7   518   
8   285   
9   584   

                                                                                                       med_terms  
0    pain,fever,chest pain,shortness of breath,redness,aspirin,hypertension,infection,chills,atrial fibrillation  
1      atrial fibrillation,pain,chest pain,fever,coumadin,shortness of breath,infection,pneumonia,redness,chills  
2       pain,chest pain,shortness of breath,fever,pneumonia,chills,infection,fevers,atrial fibrillation,vomiting  
3  pain,chest pain,fever,shortness of breath,redness,atrial fibrillation,aspirin,infection,coumadin,hypertension  
4  pain,fever,chest pain,shortness of breath,redness,aspirin,infection,atrial fibrillation,coumadin,hypertension  
5     pain,chest pain,fever,shortness of breath,chills,infection,atrial fibrillation,hypertension,fevers,aspirin  
6   chest pain,shortness of breath,atrial fibrillation,pain,fever,pneumonia,coumadin,chills,fevers,heart failure  
7       pain,shortness of breath,pneumonia,chest pain,fever,chills,atrial fibrillation,fevers,infection,vomiting  
8       pain,chest pain,shortness of breath,fever,bleeding,chills,infection,pneumonia,fevers,atrial fibrillation  
9       chest pain,shortness of breath,pain,fever,pneumonia,chills,atrial fibrillation,fevers,infection,vomiting

In [185]:
category_terms_table.rename(columns = {'index':'category'}, inplace = True) 

In [182]:
category_def={'category':['401','427','276','414','272','250','428','518','285','584'],
            'definitions':['essential hypertension','cardiac dysrhythmias','disorders of fluid,electrolyte,acid-base balance','other forms of chronic ischemic heart disease','disorders of lipoid metabolism','diabetes mellitus','heart failure','other diseases of lungs','other and unspecified anemias','acute renal failure']}

In [183]:
category_def_table=pd.DataFrame.from_dict(category_def)

In [184]:
category_def_table

category                                       definitions
0      401                            essential hypertension
1      427                              cardiac dysrhythmias
2      276  disorders of fluid,electrolyte,acid-base balance
3      414     other forms of chronic ischemic heart disease
4      272                    disorders of lipoid metabolism
5      250                                 diabetes mellitus
6      428                                     heart failure
7      518                           other diseases of lungs
8      285                     other and unspecified anemias
9      584                               acute renal failure

In [188]:
category_terms_table[['category','med_terms']]

category  \
0      401   
1      427   
2      276   
3      414   
4      272   
5      250   
6      428   
7      518   
8      285   
9      584   

                                                                                                       med_terms  
0    pain,fever,chest pain,shortness of breath,redness,aspirin,hypertension,infection,chills,atrial fibrillation  
1      atrial fibrillation,pain,chest pain,fever,coumadin,shortness of breath,infection,pneumonia,redness,chills  
2       pain,chest pain,shortness of breath,fever,pneumonia,chills,infection,fevers,atrial fibrillation,vomiting  
3  pain,chest pain,fever,shortness of breath,redness,atrial fibrillation,aspirin,infection,coumadin,hypertension  
4  pain,fever,chest pain,shortness of breath,redness,aspirin,infection,atrial fibrillation,coumadin,hypertension  
5     pain,chest pain,fever,shortness of breath,chills,infection,atrial fibrillation,hypertension,fevers,aspirin  
6   chest pain,shortness of breath,atrial fibrillation,pain,fever,pneumonia,coumadin,chills,fevers,heart failure  
7       pain,shortness of breath,pneumonia,chest pain,fever,chills,atrial fibrillation,fevers,infection,vomiting  
8       pain,chest pain,shortness of breath,fever,bleeding,chills,infection,pneumonia,fevers,atrial fibrillation  
9       chest pain,shortness of breath,pain,fever,pneumonia,chills,atrial fibrillation,fevers,infection,vomiting

In [189]:
category_def_terms=pd.merge(category_def_table,category_terms_table[['category','med_terms']],on='category')

In [190]:
category_def_terms

category                                       definitions  \
0      401                            essential hypertension   
1      427                              cardiac dysrhythmias   
2      276  disorders of fluid,electrolyte,acid-base balance   
3      414     other forms of chronic ischemic heart disease   
4      272                    disorders of lipoid metabolism   
5      250                                 diabetes mellitus   
6      428                                     heart failure   
7      518                           other diseases of lungs   
8      285                     other and unspecified anemias   
9      584                               acute renal failure   

                                                                                                       med_terms  
0    pain,fever,chest pain,shortness of breath,redness,aspirin,hypertension,infection,chills,atrial fibrillation  
1      atrial fibrillation,pain,chest pain,fever,coumadin,shortness of breath,infection,pneumonia,redness,chills  
2       pain,chest pain,shortness of breath,fever,pneumonia,chills,infection,fevers,atrial fibrillation,vomiting  
3  pain,chest pain,fever,shortness of breath,redness,atrial fibrillation,aspirin,infection,coumadin,hypertension  
4  pain,fever,chest pain,shortness of breath,redness,aspirin,infection,atrial fibrillation,coumadin,hypertension  
5     pain,chest pain,fever,shortness of breath,chills,infection,atrial fibrillation,hypertension,fevers,aspirin  
6   chest pain,shortness of breath,atrial fibrillation,pain,fever,pneumonia,coumadin,chills,fevers,heart failure  
7       pain,shortness of breath,pneumonia,chest pain,fever,chills,atrial fibrillation,fevers,infection,vomiting  
8       pain,chest pain,shortness of breath,fever,bleeding,chills,infection,pneumonia,fevers,atrial fibrillation  
9       chest pain,shortness of breath,pain,fever,pneumonia,chills,atrial fibrillation,fevers,infection,vomiting

In [194]:
diagnosis1=discharge_icd[['HADM_ID','chief complaint:','icd9_cat']]

In [197]:
diagnosis1['med_terms']=diagnosis1['chief complaint:'].progress_apply(lambda x: nlp(x).ents)

<ipython-input-197-d12798b08aac>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  diagnosis1['med_terms']=diagnosis1['chief complaint:'].progress_apply(lambda x: nlp(x).ents)


In [196]:
diagnosis1

HADM_ID  \
0      167853.0   
1      107527.0   
2      167118.0   
3      196489.0   
4      135453.0   
...         ...   
59647  135672.0   
59648  155710.0   
59649  183951.0   
59650  169165.0   
59651  157100.0   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     chief complaint:  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         

In [201]:
discharge_icd

KeyboardInterrupt: 

In [207]:
diagnosis

HADM_ID  \
0      167853.0   
1      107527.0   
2      167118.0   
3      196489.0   
4      135453.0   
...         ...   
59647  135672.0   
59648  155710.0   
59649  183951.0   
59650  169165.0   
59651  157100.0   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    discharge diagnosis:  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      

In [216]:
diagnosis1

HADM_ID  \
0      167853.0   
1      107527.0   
2      167118.0   
3      196489.0   
4      135453.0   
...         ...   
59647  135672.0   
59648  155710.0   
59649  183951.0   
59650  169165.0   
59651  157100.0   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     chief complaint:  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         

In [213]:
#diagnosis.to_csv("diagnosis_icd_medterms.csv",index=False)

In [215]:
#diagnosis1.to_csv(r"Data MIMIC III/Data2.0/complaint_icd_medterms.csv",index=False)

In [219]:
discharge_icd.columns

Index(['SUBJECT_ID', 'HADM_ID', 'CATEGORY', 'DESCRIPTION', 'ISERROR', 'TEXT',
       'text_mod', 'sec', 'split', 'service:', 'social history:',
       'family history:', 'past medical history:', 'chief complaint:',
       'discharge medications:', 'discharge disposition:',
       'discharge diagnosis:', 'allergies:', 'physical exam:', 'ICD9_CODE_x',
       'ICD10', 'ICD9_CODE_y', 'icd10_pcs', 'icd9_codes', 'icd9_cat'],
      dtype='object')

In [222]:
discharge_icd[['HADM_ID','text_mod', 'sec', 'split', 'service:', 'social history:',
       'family history:', 'past medical history:', 'chief complaint:',
       'discharge medications:', 'discharge disposition:',
       'discharge diagnosis:', 'allergies:', 'physical exam:', 'ICD9_CODE_x',
       'ICD10', 'ICD9_CODE_y', 'icd10_pcs', 'icd9_codes', 'icd9_cat']].to_csv(r"Data MIMIC III/Data2.0/text_section_icdcategory.csv",index=False)

In [3]:
complaint_icd_category=pd.read_csv(r"Data MIMIC III/Data2.0/complaint_icd_medterms.csv")

In [4]:
complaint_icd_category

HADM_ID  \
0      167853.0   
1      107527.0   
2      167118.0   
3      196489.0   
4      135453.0   
...         ...   
59641  135672.0   
59642  155710.0   
59643  183951.0   
59644  169165.0   
59645  157100.0   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     chief complaint:  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         

In [5]:
complaint_x=complaint_icd_category.loc[complaint_icd_category.icd9_cat.apply(lambda x: '401' in x)]

In [9]:
y=complaint_x.med_terms.to_list()

In [10]:
y

['(oxygen, acute dyspnea  , lethargy, dyspnea, flares, cough, chest pain, fevers, chills, orthopnea, diarrhea, confusion, neck pain, leukocytosis, lactate, solumedrol, sulfate 2 g iv x1, azithromycin, levofloxacin, cefrtiaxone 1g, hypotensive, propafol, hypotension)',
 '(fracture, ossification, slip, fracture, agitation, trauma)',
 '(hypoxia, fever, hypoxia, ceftriaxone, febrile, zosyn, tylenol, sweats, cough, upper back pain, nausea/vomiting, diarrhea, dysuria, rash, prednisone, rash, coumadin, coumadin)',
 '(seizure, headache, nausea, vomiting, bradycardia, diameter sphenoid meningioma)',
 '(aortic stenosis, aortic insufficiency, hypertension, diabetes mellitus, peripheral arterial disease s/p peripheral bypass, chest pain, chest pain, nausea, diaphoresis, pain, pain, congestive heart  failure, aspirin, furosemide, pain, osteoarthritis, chest pain, pain, pain, dyspnea, orthopnea, exertional dyspnea, dyspneic, chest pain, nose bleed, hematuria)',
 '(3-vessel disease, 3-vessel cardiac 

In [48]:
x=y[2]

In [49]:
x

'(hypoxia, fever, hypoxia, ceftriaxone, febrile, zosyn, tylenol, sweats, cough, upper back pain, nausea/vomiting, diarrhea, dysuria, rash, prednisone, rash, coumadin, coumadin)'

In [47]:
tuple(x)

('(',
 'f',
 'r',
 'a',
 'c',
 't',
 'u',
 'r',
 'e',
 ',',
 ' ',
 'o',
 's',
 's',
 'i',
 'f',
 'i',
 'c',
 'a',
 't',
 'i',
 'o',
 'n',
 ',',
 ' ',
 's',
 'l',
 'i',
 'p',
 ',',
 ' ',
 'f',
 'r',
 'a',
 'c',
 't',
 'u',
 'r',
 'e',
 ',',
 ' ',
 'a',
 'g',
 'i',
 't',
 'a',
 't',
 'i',
 'o',
 'n',
 ',',
 ' ',
 't',
 'r',
 'a',
 'u',
 'm',
 'a',
 ')')

In [50]:
def medical_terms(x):
    return re.findall(r'\(*(\w*)\,*\s*\)*',x)

In [51]:
medical_terms(x)

['hypoxia',
 'fever',
 'hypoxia',
 'ceftriaxone',
 'febrile',
 'zosyn',
 'tylenol',
 'sweats',
 'cough',
 'upper',
 'back',
 'pain',
 'nausea',
 '',
 'vomiting',
 'diarrhea',
 'dysuria',
 'rash',
 'prednisone',
 'rash',
 'coumadin',
 'coumadin',
 '']

In [15]:
diagnosis_icd_category=pd.read_csv(r"Data MIMIC III/Data2.0/diagnosis_icd_medterms.csv")

In [16]:
diagnosis_icd_category

HADM_ID  \
0      167853.0   
1      107527.0   
2      167118.0   
3      196489.0   
4      135453.0   
...         ...   
59641  135672.0   
59642  155710.0   
59643  183951.0   
59644  169165.0   
59645  157100.0   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    discharge diagnosis:  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      